In [1]:
from ultralytics import YOLO
import cv2
from matplotlib import pyplot as plt



In [4]:
# Vehicle detection model (COCO)
vehicle_model = YOLO("yolov8n.pt")

# Your ANPR model (trained on number plates)
plate_model = YOLO(r"C:/Users/ADMIN/Downloads/ANPR-ATCC-Infosys-main/ANPR-ATCC-Infosys-main/weights/best.pt")



In [5]:
import easyocr
reader = easyocr.Reader(['en'])

def extract_plate_text(crop):
    result = reader.readtext(crop, detail=0)
    return result[0] if len(result) > 0 else ""


Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


In [17]:
import cv2
from ultralytics import YOLO
import easyocr
from IPython.display import Video
import imageio

# ---------------------------
# Load Models
# ---------------------------
vehicle_model = YOLO("yolov8n.pt")  # COCO model for vehicles
plate_model = YOLO(r"C:/Users/ADMIN/Downloads/ANPR-ATCC-Infosys-main/ANPR-ATCC-Infosys-main/weights/best.pt")
reader = easyocr.Reader(['en'])

# Vehicle class map
class_map = {
    2: "car",
    3: "bike",
    5: "bus",
    7: "truck",
    9: "traffic_light"
}

# Input video
input_video = r"C:\Users\ADMIN\Downloads\ATCC.zip\BDDA\test\camera_videos\88.mp4"
output_video = r"D:\output1_atcc.mp4"

cap = cv2.VideoCapture(input_video)

# Get video properties
fps = int(cap.get(cv2.CAP_PROP_FPS))
if fps == 0:
    fps = 25  # fallback
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

# List to store processed frames
frames_list = []

# ---------------------------
# Process Video Frames
# ---------------------------
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # 1) VEHICLE DETECTION
    vehicle_results = vehicle_model.predict(frame, verbose=False)[0]

    for box in vehicle_results.boxes:
        cls = int(box.cls[0])

        if cls in class_map:
            label = class_map[cls]
            x1, y1, x2, y2 = map(int, box.xyxy[0])

            # Draw green bounding box for vehicle
            cv2.rectangle(frame, (x1, y1), (x2, y2), (0,255,0), 2)
            cv2.putText(frame, label, (x1, y1-10),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0,255,0), 2)

            # Crop vehicle area
            vehicle_crop = frame[y1:y2, x1:x2]

            # 2) NUMBER PLATE DETECTION
            plate_results = plate_model.predict(vehicle_crop, verbose=False)[0]

            for p in plate_results.boxes:
                px1, py1, px2, py2 = map(int, p.xyxy[0])

                # Crop plate
                plate_crop = vehicle_crop[py1:py2, px1:px2]

                # OCR text detection
                text = reader.readtext(plate_crop, detail=0)
                plate_text = text[0] if len(text) > 0 else ""

                # Draw red box for number plate
                cv2.rectangle(vehicle_crop, (px1, py1), (px2, py2), (0,0,255), 2)

                # Put plate text above vehicle box
                cv2.putText(frame, plate_text, (x1, y1 - 40),
                            cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0,0,255), 2)

    # Convert frame to RGB for imageio
    frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    frames_list.append(frame_rgb)

cap.release()

# ---------------------------
# Save Video using imageio (MP4 H.264)
# ---------------------------
imageio.mimsave(output_video, frames_list, fps=fps, codec="libx264")
print("🎉 OUTPUT VIDEO SAVED AS:", output_video)

# Display video in Jupyter
Video(output_video, embed=True)


Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


🎉 OUTPUT VIDEO SAVED AS: D:\output1_atcc.mp4


In [18]:
import cv2
from ultralytics import YOLO
import easyocr
from IPython.display import Video
import imageio
import os

# ---------------------------
# Load Models
# ---------------------------
vehicle_model = YOLO("yolov8n.pt")  # COCO vehicle detection
plate_model = YOLO(r"C:/Users/ADMIN/Downloads/ANPR-ATCC-Infosys-main/ANPR-ATCC-Infosys-main/weights/best.pt")
reader = easyocr.Reader(['en'])

# Vehicle class map
class_map = {
    2: "car",
    3: "bike",
    5: "bus",
    7: "truck",
    9: "traffic_light"
}

# ---------------------------
# Input & Output Video Paths
# ---------------------------
input_video = r"C:\Users\ADMIN\Downloads\ATCC.zip\BDDA\test\camera_videos\88.mp4"

# Output folder (created automatically)
output_folder = r"D:\ATCC_outputs"
os.makedirs(output_folder, exist_ok=True)
output_video = os.path.join(output_folder, "output_atcc.mp4")

# ---------------------------
# Open Video
# ---------------------------
cap = cv2.VideoCapture(input_video)

# Video properties
fps = int(cap.get(cv2.CAP_PROP_FPS))
if fps == 0:
    fps = 25
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

# List to store frames for imageio
frames_list = []

# ---------------------------
# Processing Loop
# ---------------------------
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # 1) VEHICLE DETECTION
    vehicle_results = vehicle_model.predict(frame, verbose=False)[0]

    for box in vehicle_results.boxes:
        cls = int(box.cls[0])
        if cls in class_map:
            label = class_map[cls]
            x1, y1, x2, y2 = map(int, box.xyxy[0])

            # Draw green bounding box for vehicle
            cv2.rectangle(frame, (x1, y1), (x2, y2), (0,255,0), 2)
            cv2.putText(frame, label, (x1, y1-10),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0,255,0), 2)

            # Crop vehicle area
            vehicle_crop = frame[y1:y2, x1:x2]

            # 2) NUMBER PLATE DETECTION
            plate_results = plate_model.predict(vehicle_crop, verbose=False)[0]

            for p in plate_results.boxes:
                px1, py1, px2, py2 = map(int, p.xyxy[0])

                # Crop plate
                plate_crop = vehicle_crop[py1:py2, px1:px2]

                # OCR text detection
                text = reader.readtext(plate_crop, detail=0)
                plate_text = text[0] if len(text) > 0 else ""

                # Draw red box for plate
                cv2.rectangle(vehicle_crop, (px1, py1), (px2, py2), (0,0,255), 2)

                # Put plate text above green vehicle box
                cv2.putText(frame, plate_text, (x1, y1 - 40),
                            cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0,0,255), 2)

    # Convert BGR to RGB for imageio
    frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    frames_list.append(frame_rgb)

cap.release()

# ---------------------------
# Save MP4 video using imageio (H.264)
# ---------------------------
imageio.mimsave(output_video, frames_list, fps=fps, codec="libx264")
print("🎉 OUTPUT VIDEO SAVED SUCCESSFULLY:", output_video)

# Display video in Jupyter Notebook
Video(output_video, embed=True)


Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


🎉 OUTPUT VIDEO SAVED SUCCESSFULLY: D:\ATCC_outputs\output_atcc.mp4


In [19]:
input_video = r"C:\Users\ADMIN\Downloads\ATCC.zip\BDDA\test\camera_videos\88.mp4"


In [20]:
cap = cv2.VideoCapture(input_video)
if not cap.isOpened():
    print("❌ ERROR: Video file not found or cannot be opened!")
else:
    print("✅ Video loaded successfully!")


❌ ERROR: Video file not found or cannot be opened!


In [21]:
import cv2
from ultralytics import YOLO
import easyocr
from IPython.display import Video
import imageio
import os

# ---------------------------
# Load Models
# ---------------------------
vehicle_model = YOLO("yolov8n.pt")  # COCO vehicle detection
plate_model = YOLO(r"C:/Users/ADMIN/Downloads/ANPR-ATCC-Infosys-main/ANPR-ATCC-Infosys-main/weights/best.pt")
reader = easyocr.Reader(['en'])

# Vehicle class map
class_map = {
    2: "car",
    3: "bike",
    5: "bus",
    7: "truck",
    9: "traffic_light"
}

# ---------------------------
# Input & Output Video Paths
# ---------------------------
# Make sure you extract the video from ZIP first
input_video = r"C:\Users\ADMIN\Videos\88.mp4"  # <-- update with extracted video path

# Output folder (created automatically)
output_folder = r"D:\ATCC_outputs"
os.makedirs(output_folder, exist_ok=True)
output_video = os.path.join(output_folder, "output_atcc.mp4")

# ---------------------------
# Check Video Path
# ---------------------------
cap = cv2.VideoCapture(input_video)
if not cap.isOpened():
    raise FileNotFoundError(f"❌ ERROR: Video file not found or cannot be opened!\nCheck path: {input_video}")
else:
    print("✅ Video loaded successfully!")

# Video properties
fps = int(cap.get(cv2.CAP_PROP_FPS))
if fps == 0:
    fps = 25  # fallback
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

# List to store processed frames
frames_list = []

# ---------------------------
# Processing Loop
# ---------------------------
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # 1) VEHICLE DETECTION
    vehicle_results = vehicle_model.predict(frame.copy(), verbose=False)[0]

    for box in vehicle_results.boxes:
        cls = int(box.cls[0])
        if cls in class_map:
            label = class_map[cls]
            x1, y1, x2, y2 = map(int, box.xyxy[0])

            # Draw green bounding box for vehicle
            cv2.rectangle(frame, (x1, y1), (x2, y2), (0,255,0), 2)
            cv2.putText(frame, label, (x1, y1-10),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0,255,0), 2)

            # Crop vehicle area
            vehicle_crop = frame[y1:y2, x1:x2]

            # 2) NUMBER PLATE DETECTION
            plate_results = plate_model.predict(vehicle_crop.copy(), verbose=False)[0]

            for p in plate_results.boxes:
                px1, py1, px2, py2 = map(int, p.xyxy[0])

                # Crop plate
                plate_crop = vehicle_crop[py1:py2, px1:px2]

                # OCR text detection
                text = reader.readtext(plate_crop, detail=0)
                plate_text = text[0] if len(text) > 0 else ""

                # Draw red box for plate
                cv2.rectangle(vehicle_crop, (px1, py1), (px2, py2), (0,0,255), 2)

                # Put plate text above green vehicle box
                cv2.putText(frame, plate_text, (x1, y1 - 40),
                            cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0,0,255), 2)

    # Convert BGR to RGB for imageio
    frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    frames_list.append(frame_rgb)

cap.release()

# ---------------------------
# Save MP4 video using imageio (H.264)
# ---------------------------
imageio.mimsave(output_video, frames_list, fps=fps, codec="libx264")
print("🎉 OUTPUT VIDEO SAVED SUCCESSFULLY:", output_video)

# Display video in Jupyter Notebook
Video(output_video, embed=True)


Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


✅ Video loaded successfully!


C:\Users\ADMIN\AppData\Local\Programs\Python\Python313\Lib\site-packages\torch\utils\data\dataloader.py:668: UserWarning: 'pin_memory' argument is set as true but no accelerator is found, then device pinned memory won't be used.
  warnings.warn(warn_msg)


🎉 OUTPUT VIDEO SAVED SUCCESSFULLY: D:\ATCC_outputs\output_atcc.mp4


In [ ]:
import cv2
from ultralytics import YOLO
import easyocr
from IPython.display import Video
import imageio
import os

# ---------------------------
# Load Models
# ---------------------------
vehicle_model = YOLO("yolov8n.pt")  # COCO vehicle detection
plate_model = YOLO(r"C:/Users/ADMIN/Downloads/ANPR-ATCC-Infosys-main/ANPR-ATCC-Infosys-main/weights/best.pt")
reader = easyocr.Reader(['en'])

# Vehicle class map
class_map = {
    2: "car",
    3: "bike",
    5: "bus",
    7: "truck",
    9: "traffic_light"
}

# Initialize counters
total_counts = {v:0 for v in class_map.values()}
processed_ids = set()  # to avoid double-counting same vehicle

# ---------------------------
# Input & Output Video Paths
# ---------------------------
input_video = r"C:\Users\ADMIN\Videos\88.mp4"  # update path
output_folder = r"D:\ATCC_outputs"
os.makedirs(output_folder, exist_ok=True)
output_video = os.path.join(output_folder, "output_atcc_final.mp4")

# ---------------------------
# Check Video
# ---------------------------
cap = cv2.VideoCapture(input_video)
if not cap.isOpened():
    raise FileNotFoundError(f"❌ Video file not found! Check path: {input_video}")
else:
    print("✅ Video loaded successfully!")

fps = int(cap.get(cv2.CAP_PROP_FPS)) or 25
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
frames_list = []

# ---------------------------
# Process Frames
# ---------------------------
while True:
    ret, frame = cap.read()
    if not ret:
        break

    vehicle_results = vehicle_model.predict(frame.copy(), verbose=False)[0]

    for box in vehicle_results.boxes:
        cls = int(box.cls[0])
        if cls in class_map:
            label = class_map[cls]
            x1, y1, x2, y2 = map(int, box.xyxy[0])

            # Draw vehicle bounding box
            cv2.rectangle(frame, (x1, y1), (x2, y2), (0,255,0), 2)
            cv2.putText(frame, label, (x1, y1-10),
                        cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0,255,0), 2)

            # Count unique vehicles
            box_id = (cls, x1, y1, x2, y2)
            if box_id not in processed_ids:
                total_counts[label] += 1
                processed_ids.add(box_id)

            # Crop vehicle
            vehicle_crop = frame[y1:y2, x1:x2]

            # Number plate detection
            plate_results = plate_model.predict(vehicle_crop.copy(), verbose=False)[0]
            for p in plate_results.boxes:
                px1, py1, px2, py2 = map(int, p.xyxy[0])
                plate_crop = vehicle_crop[py1:py2, px1:px2]

                text = reader.readtext(plate_crop, detail=0)
                plate_text = text[0] if len(text) > 0 else ""

                # Draw plate (red box)
                cv2.rectangle(vehicle_crop, (px1, py1), (px2, py2), (0,0,255), 2)
                cv2.putText(frame, plate_text, (x1, y1-40),
                            cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0,0,255), 2)

    # Store frame
    frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    frames_list.append(frame_rgb)

cap.release()

# ---------------------------
# Save output MP4 video
# ---------------------------
imageio.mimsave(output_video, frames_list, fps=fps, codec="libx264")
print(f"🎉 OUTPUT VIDEO SAVED SUCCESSFULLY: {output_video}")

# ---------------------------
# Display final vehicle counts
# ---------------------------
print("\n===== TOTAL VEHICLE COUNTS IN VIDEO =====")
for vehicle, count in total_counts.items():
    print(f"{vehicle.capitalize()}: {count}")
print("========================================")

# Display video in Jupyter
Video(output_video, embed=True)
